In [ ]:
from trafilatura.spider import focused_crawler
from trafilatura import fetch_url, extract
from tqdm import tqdm
import tiktoken

from pathlib import Path
from urllib.parse import urlparse
from markitdown import MarkItDown
import requests
import unicodedata


enc = tiktoken.encoding_for_model("gpt-4o")
md = MarkItDown()


In [ ]:
NON_HTML = {".pdf", ".docx", ".pptx", ".xlsx", ".odt", ".ods", ".odp"}

def convert_to_markdown(src: str) -> str | None:
    try:
        u   = urlparse(src)
        ext = Path(u.path).suffix.lower()
        if u.scheme in ("", "file") or ext in NON_HTML:
            return md.convert(src).text_content
        return extract(fetch_url(src), include_formatting=True)# Markdown形式で抽出(ABEJAのやり方を参考に)
    except Exception:
        return None


In [ ]:
add_urls = [
    "https://www.fsa.go.jp/common/law/guide/city/index.html",
    "https://www.fsa.go.jp/common/law/guide/city/01.html",
    "https://www.fsa.go.jp/common/law/guide/city/02.html",
    "https://www.fsa.go.jp/common/law/guide/city/03a.html",
    "https://www.fsa.go.jp/common/law/guide/city/03b.html",
    "https://www.fsa.go.jp/common/law/guide/city/03c1.html",
    "https://www.fsa.go.jp/common/law/guide/city/03c2.html",
    "https://www.fsa.go.jp/common/law/guide/city/03d1.html",
    "https://www.fsa.go.jp/common/law/guide/city/03d2.html",
    "https://www.fsa.go.jp/common/law/guide/city/04.html",
    "https://www.fsa.go.jp/common/law/guide/city/05.html",
    "https://www.fsa.go.jp/common/law/guide/city/06.html",
    "https://www.fsa.go.jp/common/law/guide/city/07.html",
    "https://www.fsa.go.jp/common/law/guide/city/08.html",
    "https://www.fsa.go.jp/common/law/guide/city/9.html",
    "https://www.fsa.go.jp/common/law/guide/city/10.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/index.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/01.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/02.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/03.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/04a.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/04b.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/05.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/06.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/07.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/08.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/09.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/10.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/11.html",
    "https://www.fsa.go.jp/common/law/guide/kinyushohin/12.html",
    "https://www.fsa.go.jp/policy/basel_ii/baselgaiyou-6.pdf",
    "https://www.ppc.go.jp/personalinfo/legal/kinyubunya_GL/",
    "https://www.fsa.go.jp/news/r6/sonota/20241004/18.pdf",
    "https://www.fsa.go.jp/common/law/amlcft/211122_amlcft_guidelines.pdf",
    ]

# # Webクローリング
# to_visit, known_links = focused_crawler("https://www.fsa.go.jp/")
# urls = to_visit
# for url in add_urls:
#     if url not in to_visit:
#         urls.append(url)

urls = add_urls
print(f"Total URLs to process: {len(urls)}")

Total URLs to process: 34


In [75]:
BASE = "https://laws.e-gov.go.jp/api/2/law_data"
HEAD = {"Accept": "application/json"}

def flatten(node, sep=""):
    """children を再帰的にたどり文字列を sep で連結して返す"""
    if isinstance(node, str):
        return node
    if isinstance(node, dict):
        node = node.get("children", [])
    try:
        return sep.join(flatten(c, sep) for c in node)
    except TypeError:
        return ""

def fetch_laws(law_ids, *, sep="\n"):
    """
    law_ids : iterable[str]  …  LAW_ID のリスト/タプル
    sep     : str           …  子ノード連結用の区切り文字
    戻り値   : {LAW_ID: text, ...}
    """
    texts = {}
    for law_id in law_ids:
        data = requests.get(
            f"{BASE}/{law_id}",
            params={"law_full_text_format": "json"},
            headers=HEAD
        ).json()
        text = unicodedata.normalize("NFKC",
                                     flatten(data["law_full_text"], sep))
        texts[law_id] = text
    return texts

In [ ]:
# 
LAW_IDS = [
    "323AC0000000025_20250601_504AC0000000068",
    "356AC0000000059_20250601_504AC0000000068",
    "407AC0000000105_20250601_504AC0000000068",
    "358AC1000000032_20250601_504AC0000000068",
    "419AC0000000022_20250601_504AC0000000068",
    ]

all_texts = fetch_laws(LAW_IDS)

In [72]:
results = []
# URL からの変換
for src in tqdm(urls):
    text_md = convert_to_markdown(src)
    if not text_md:
        print(f"[Error] 変換失敗: {src}")
        continue
    tokens = enc.encode(text_md)
    results.append({"url": src, "text": text_md, "tokens": len(tokens)})

# 法令データからの変換
for src in tqdm(all_texts.keys()):
    text_md = all_texts[src]
    if not text_md:
        print(f"[Error] 変換失敗: {src}")
        continue
    tokens = enc.encode(text_md)
    results.append({"url": src, "text": text_md, "tokens": len(tokens)})


100%|██████████| 5/5 [00:00<00:00,  8.97it/s]


In [73]:
# テキストを連結し、またトークン数の合計を計算する
combined_text = "\n".join([r["text"] for r in results])
total_tokens = sum(r["tokens"] for r in results)
# 結果を表示
print(f"Total URLs: {len(results)}")
print(f"Total tokens: {total_tokens}")

Total URLs: 39
Total tokens: 2453711


In [74]:
results

[{'url': 'https://www.fsa.go.jp/common/law/guide/city/index.html',
  'text': '主要行等向けの総合的な監督指針 令和７年６月\nI 基本的考え方\nII 主要行等の検査・監督に係る事務処理上の留意点\n- II －１ 検査・監督事務に係る基本的考え方\n- II －１－１ 検査・監督事務の進め方\n- II －１－２ 検査・監督事務の具体的手法\n- II －１－３ 品質管理\n- II －１－４ 財務局との連携\n- II －１－５ 預金保険機構が行う検査との連携\n- II －１－６ 個別銀行に関する行政報告等\n- II －１－７ 銀行等が提出する申請書等における記載上の留意点\n- II －１－８ 書面・対面による手続きについての留意点\n- II －１－９ 申請書等を提出するに当たっての留意点\n- II －２ 銀行に関する苦情・情報提供等\n- II －２－１ 相談・苦情等を受けた場合の対応\n- II －２－２ 金融サービス利用者相談室との連携\n- II －２－３ 金融サービス利用者相談室で受け付けた情報のうち、いわゆる貸し渋り・貸し剥がしとして提供された情報に係る監督上の対応\n- II －２－４ 預金口座を利用した架空請求等預金口座の不正利用に関する情報を受けた場合の対応\n- II －３ 法令解釈等の照会を受けた場合の対応\n- II －３－１ 照会を受ける内容の範囲\n- II －３－２ 照会に対する回答方法\n- II －３－３ 法令適用事前確認手続（ノーアクションレター制度）\n- II －３－４ グレーゾーン解消制度\n- II －３－５ 預金等に対する当局への照会等への対応\n- II －４ 行政指導等を行う際の留意点等\n- II －４－１ 行政指導等を行う際の留意点\n- II －４－２ 面談等を行う際の留意点\n- II －５ 行政処分等を行う際の留意点等\n- II －５－１ 行政処分（不利益処分）に関する基本的な事務の流れについて\n- II －５－１－１ 行政処分\n- II －５－１－２ 法第26条に基づく業務改善命令の履行状況の報告義務の解除\n- II －５－２ 行政手続法との関係等\n- II －５－３ 意見交換制度\n- II －５－４ 